In [1]:
import sys
sys.path.append('../')
import joblib

from scipy.signal import savgol_filter

from Modules.Utils.Imports import *
from Modules.Utils.DRUMS_Lasso import *
from Modules.Utils.GetLowestGPU import *
import Modules.Loaders.DataFormatter as DF

from Notebooks.utils import get_case_name
from queue import PriorityQueue

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
device = torch.device(GetLowestGPU(pick_from=[0,1,2,3]))
# helper functions
def to_torch(x):
    return torch.from_numpy(x).float().to(device)
def to_numpy(x):
    return x.detach().cpu().numpy()

Device set to cpu


In [4]:
# instantiate BINN model parameters and path
path = '../Data/covasim_data/drums_data/'

population = int(500e3)
test_prob = 0.1
trace_prob = 0.3
keep_d = True
retrain = False
dynamic = True
masking = 1
multiple = True
parallelb = True
n_runs = 64
chi_type = 'piecewise'

case_name = get_case_name(population, test_prob, trace_prob, keep_d, dynamic=dynamic, chi_type=chi_type)

In [5]:
if not masking==0:
    if masking==1:
        case_name = case_name + '_maskingdem'
    elif masking==2:
        case_name = case_name + '_maskinguni'
    elif masking==3:
        case_name = case_name + '_maskingnorm'

if multiple:
    params = DF.load_covasim_data(path, population, test_prob, trace_prob, keep_d, case_name + '_' + str(n_runs), plot=False)
else:
    params = DF.load_covasim_data(path, population, test_prob, trace_prob, keep_d, case_name, plot=False)

In [6]:
# multiple==True and parallelb==False means that data is a list and not normalized
if multiple and not parallelb:
    data = np.mean(params['data'], axis=0)
    data = (data / params['population'])
    avg_masking = np.mean(params['avg_masking'], axis=0)
    avg_masking = (avg_masking / params['population'])
# multiple==True and parallelb==True means that the data is a 2d array and normalized
elif multiple and parallelb:
    data = params['data'] # parallel simulations store normalized data
    avg_masking = params['avg_masking']
# otherwise, the data is from a single simulation and is not normalized
else:
    data = params['data']
    data = (data / params['population']).to_numpy()
    avg_masking = params['avg_masking']
    avg_masking = (avg_masking / params['avg_masking'])
    
params.pop('data')

N = len(data)
t_max = N - 1
t = np.arange(N)[:,None]

tracing_array = params['tracing_array']

In [7]:
# estimate dmdmt
window_size = 15
degree = 3
mt = to_torch(savgol_filter(avg_masking, window_size, degree, deriv=1, axis=0))
#plt.plot(t, mt)

***
### LASSO on $M$

In [9]:
def get_best_num_comps(num_comps=-1, pq=None):
    if pq.empty():
        raise Exception('The Priority Queue given is empty')
    bl_dict = pq.get()[-1]
    if num_comps==-1:
        return bl_dict
    if 'f ' in bl_dict['Equation'].split('+'):
        return bl_dict
    if len(bl_dict['Equation'].split('+')) - 1 <= num_comps:
        return bl_dict
    
    good_eq = False
    while not good_eq and not pq.empty():
        cand = pq.get()[-1]
        curr_num = len(cand['Equation'].split('+')) - 1
        if curr_num <= num_comps:
            good_eq = True
            return cand
    if not good_eq:
        raise Exception('No equation with that number of components was found')

In [13]:
comps = list('STEAYDQRF')
X_dict = {key : value for key, value in zip(comps, data.T)}
alphas_list = np.linspace(float(1e-8), float(1e-6), num=5000)

eq_set = set()
eq_q = PriorityQueue()
min_comps = 1000

for i in alphas_list:
    lasso_dict = DRUMS_Lasso(X_dict, mt, intercept=True, alphas=np.array([i]))
    if not lasso_dict['Equation'] in eq_set:
        eq_set.add(lasso_dict['Equation'])
        eq_q.put((lasso_dict['MSE'], i, lasso_dict['Equation'], lasso_dict))
        min_comps = len(lasso_dict['Equation'].split('+')) - 1
        if 'f ' in lasso_dict['Equation'].split('+'):
                break

c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 2.9021436321154747e-06, tolerance: 1.4978412571290064e-07
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 3.352511720580703e-05, tolerance: 3.3812073325684545e-07
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\envs\reu_env\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:620: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 9.244519488725168e-05, tolerance: 3.0967398839061566e-07
  model = cd_fast.enet_coordinate_descent_gram(
c:\Users\Teddy\anaconda3\en

In [14]:
bl_dict = get_best_num_comps(pq=eq_q)
max_comps = len(bl_dict['Equation'].split('+')) - 1
best_list = [bl_dict]
for i in reversed(range(min_comps, max_comps)):
    nb_dict = get_best_num_comps(num_comps=i, pq=eq_q)
    best_list.append(nb_dict)

In [15]:
if not os.path.exists(path + '/mt_eq_coef'):
    os.makedirs(os.path.join(path, 'mt_eq_coef'))
    
file_path = path  + '/mt_eq_coef'

for i, elem in enumerate(reversed(best_list)):
    nb_file_name = case_name + '_' + str(n_runs) + '_sparse_coef_' + str(i + min_comps) + 'comps'
    joblib.dump(elem, os.path.join(file_path, nb_file_name), compress=True)